In [ ]:
# 使用《复杂》中罗比扫地机器人的例子，进行遗传算法编程
# 场景说明：
# 场地总共是10×10个格子，每个格子可能有三种情况：
#    0. 空
#    1. 罐子
#    2. 墙
# 罗比是一个机器人，他每次都只能看到周围和当前格子的情况
# 也就是其周围“上下左右中”的情况，按照顺序记入一个列表：
#    [0, 0, 0, 0, 0] -> 周围都是空的
#    [2, 0, 0, 1, 0] -> 上面是墙，右面有罐子
# 针对不同情况他的策略是:
#    0:向上走
#    1:向下走
#    2:向左走
#    3:向右走
#    4:随机走
#    5:什么都不做
#    6:捡罐子
# 总共7种策略
#
# 由于需要计算染色体(chromosome)的代表性，所以我们需要确定染色体的长度：
#    罗比能看到范围的情况 3 ^ 5 = 243 种，所以染色体需要243位的长度
#    我们对应染色体列表的chromosome[0]~chromosome[242]分别对应
#    [0,0,0,0,0], [0,0,0,0,0,1], [0,0,0,0,2], ~ ,[2,2,2,2,1], [2,2,2,2,2]
#    染色体的值 chromosome[n] 取值于 0 ~ 6 共 7 种策略。
# 所以需要在总共 7 ^ 243 种策略中寻找最优策略。
# 比如：
#    染色体m为chromosom[m] = "56132....62312" 长度为243, 其意义为
#    [0,0,0,0,0] 采取 5 也就是 什么都不做的策略
#    [0,0,0,0,1] 采取 6 也就是 拣罐子
#    [0,0,0,0,2] 采取 1 也就是 向右走
#    [0,0,0,1,0] 采取 3 也就是 向后走
#    [0,0,0,1,1] 采取 2 也就是 向前走
# 以此类推
# 优化的目的是找到最佳个体，其实就是染色体序列，使其的表现最佳。染色体是基因组合，种群其实就是染色体组合。
#
# 评分策略：
#    有罐子捡起 +10
#    没罐子却捡 -1
#    撞墙 -5

In [1]:
import math, random

In [11]:
class Population:
    def __init__(self, map_size, size, chrom_size, cp, mp, gen_max, max_step=200, g_loop=100):
        # 种群信息
        self.individuals = [] # 个体集合
        self.fitness = [] # 个体适应度集合
        self.selector_probability = [] # 个体选择概率集合
        self.new_individuals = [] # 新一代个体集合
        self.elitists = {}
        
        self.elitist = {'chromosome': [0, 0], 'fitness': 0, 'age': 0} # 最佳个体信息
        
        self.size = size # 种群包含个体数量
        self.chromosome_size = chrom_size # 染色体长度
        self.crossover_probability = cp # 个体间染色体交叉概率
        self.mutation_probability = mp # 个体变异概率
        
        self.generation_max = gen_max # 进化最大世代数
        self.age = 0 # 种群当前世代
        self.maxStep = max_step
        self.gen_loop = g_loop
        
        self.map_dim = map_size
        self.map = self.genMap()
        self.actions = 7
        self.sample_space = 243
        self.strategyMX = {} # 用strategyMX来指定染色体中的基因
        self._genStrategy(self.sample_space)
        self.log = []
        
        self.act = {
            0: "up",
            1: "down",
            2: "left",
            3: "right",
            4: "rand",
            5: "none",
            6: "pick"
        }
        self.status = {
            0: "none",
            1: "can",
            2: "wall"
        }
        self.pickpunish = {
            0: -1,
            # 应该不会出现人在墙上
            2: -1,
            1: 10
        }
        
        for i in range(self.size):
            tmpArr = []
            for n in range(self.sample_space):
                tmpArr.append(random.randint(0, self.actions-1))
            self.individuals.append(tmpArr)
            self.fitness.append(0)
            self.selector_probability.append(0)
            self.new_individuals.append([])

    def _genStrategy(self, sNum):
            # act = list(range(self.actions))
            tmp = [0, 0, 0, 0, 0]
            # 3^5=243种枚举策略
            # self.strategyMX[tuple(tmp)] = act
            self.strategyMX[tuple(tmp)] = 0
            # sNum -= 1
            for i in range(1, sNum):
                tmp = self._addEle(tmp)
                self.strategyMX[tuple(tmp)] = i
            return self.strategyMX

    def _addEle(self, tmp):
        m = len(tmp)
        while m >=0 :
            tmp[m-1] += 1
            if tmp[m-1] > 2:
                tmp[m-1] = 0
                m = m - 1
            else:
                return tmp
            
    def _setItem(self, items=[2, 1, 0], probDis=[0, 0.5, 0.5]):
        # 参数是概率分布数组
        p = random.uniform(0, 1)
        cumulative_probability = 0.0
        for item, item_prob in zip(items, probDis):
            cumulative_probability += item_prob
            if p < cumulative_probability:
                return item
    def showMap(self, tmpmap):
        for i in tmpmap:
            print(" ".join(map(str, i)))
    
    def genMap(self):
        tmpmap = []
        # 四边为墙
        upper = [2] * self.map_dim
        bottom = [2] * self.map_dim
        tmpmap.append(upper)
        for row in range(self.map_dim-2):
            tmpmap.append([0] * self.map_dim)
            tmpmap[row + 1][0] = 2
            for col in range(self.map_dim-2):
                tmpmap[row + 1][col+1] = self._setItem()
            tmpmap[row + 1][col+2] = 2
        tmpmap.append(bottom)
        return tmpmap
    
    def lookAround(self, pos, nowMap):
        # 只能看到上下左右中, pos是(x, y), 但要注意其实 x是纵轴，y是横轴
        x, y = pos
        return nowMap[x-1][y], nowMap[x+1][y], nowMap[x][y-1], nowMap[x][y+1], nowMap[x][y]
    
    def score(self, act, pos, nowMap):
        # 这里实际上是完成了解码和评估两步
        # 解决从染色体到具体得分的过程
        pos = list(pos)
#         print(pos, act)
        if act == "rand":
            act = ["up", "down", "left", "right", "pick", "none"][random.randint(0, 5)]
        scoreHash = {
            # “动作”: [x或者y, -1或者1] 用-1乘以这个值完成加减的转换
            "up": [0,1],
            "down": [0, -1],
            "left": [1, 1],
            "right": [1, -1],
            "none": [0, 0],
            #"rand": [random.randint(0, 1), [-1, 1][random.randint(0, 1)]],
            "pick": [0, 0]
        }
        posIDX = scoreHash[act][0]
        posDelta = scoreHash[act][1]
        pos[posIDX] += -1 * posDelta
        if act == "pick":
            sc = self.pickpunish[nowMap[pos[0]][pos[1]]]
            if nowMap[pos[0]][pos[1]] == 1:
#                 print("Picked", nowMap[pos[0]][pos[1]])
                nowMap[pos[0]][pos[1]] = 0
            return sc, tuple(pos)
        elif nowMap[pos[0]][pos[1]] == 2:
            # 墙壁无法走过去，所以要还原位置，其实很简单只要把乘数-1去掉就好
            pos[posIDX] += posDelta
            return -15, tuple(pos)
        return 0, tuple(pos)
    
    def _initPos(self):
#         return 1, 1
        return random.randint(1, self.map_dim-2), random.randint(1, self.map_dim-2)
    
    
    def genLife(self, nowChromo):
        newMap = self.genMap()
#         print("".join(map(str, nowChromo)))
#         self.showMap(newMap)
        pos = self._initPos()
        # print(pos)
        score = 0
        for i in range(self.maxStep):
            envStatus = self.lookAround(pos, newMap)
            genePOS = self.strategyMX[envStatus]
            score_gen, pos = self.score(self.act[nowChromo[genePOS]], pos, newMap)
            score += score_gen
#             print(envStatus, genePOS, nowChromo[genePOS], score)
        return score

    def fitness_func(self):
        for i in range(self.generation_max):
            for no, individual in enumerate(self.individuals):
                score = 0
                for n in range(self.gen_loop):
                    score += self.genLife(individual)
                self.fitness[no] = score / self.gen_loop
            self.evaluate()
            self.getElitist(i)
            # print(self.selector_probability)
            # print(sum(self.fitness)/len(self.fitness))
            self.log.append([i, max(self.fitness), sum(self.fitness)/len(self.fitness), min(self.fitness)])
            self.evolve()
            print(i, ": ".join(map(str, self.log[-1])))
            
        return True
    
    def evaluate(self):
        sp = self.selector_probability
        worst_score = 15 * self.maxStep
        minFIT = abs(min(self.fitness))
#         ft_sum = sum(self.fitness) + worst_score * self.size
        ft_sum = sum(self.fitness) + minFIT * self.size
        
        for i in range(self.size):
#             sp[i] = (self.fitness[i] + worst_score) / ft_sum
            sp[i] = (self.fitness[i] + minFIT) / ft_sum
        
        old = 0
#         for n, p in sorted(enumerate(sp), key= lambda x: x[1]):
#             old += p
#             sp[n] = old 
        for i in range(self.size):
            sp[i] += sp[i-1]
    
    def select(self):
        t = random.random()
        for n, p in enumerate(self.selector_probability):
            if p > t:
                break
        return n
    
    def showCh(self, chromo):
        return "".join(map(str, chromo))
    
    def cross(self, chromo1, chromo2):
        p = random.random()
        cross_pos = random.randint(0, self.sample_space-1)
        new_chromo1 = chromo1[:]
        new_chromo2 = chromo2[:]
        if chromo1 != chromo2 and p < self.crossover_probability:
            # 按照书上的交叉，是随机的点进行交换
            new_chromo1, new_chromo2 = chromo1[: cross_pos], chromo2[: cross_pos]
            new_chromo1.extend(chromo2[cross_pos:])
            new_chromo2.extend(chromo1[cross_pos:])
        return new_chromo1, new_chromo2
    
    def mutate(self, chromo):
        new_chromo = chromo[:]
        p = random.random()
        # print(p, self.mutation_probability)
        if p < self.mutation_probability:
            mutate_idx = random.randint(0, self.sample_space-1)
            mutate_val = list(range(self.actions))[random.randint(0, self.actions-1)]
            # print(mutate_idx, mutate_val, chromo[mutate_idx])
            new_chromo[mutate_idx] = mutate_val
        return new_chromo
    
    def evolve_double(self):
        i = 2
        while True:
            s_chromo1 = self.select()
            s_chromo2 = self.select()
#             print(s_chromo1, s_chromo2)
            (n_chromo1, n_chromo2) = self.cross(
                self.individuals[s_chromo1],
                self.individuals[s_chromo2])
            self.new_individuals[i] = self.mutate(n_chromo1)
            self.new_individuals[i+1] = self.mutate(n_chromo2)
            i += 2
            if i >= self.size:
                break
        self.new_individuals[0] = self.elitists["chromosome"][0][:]
        self.new_individuals[1] = self.elitists["chromosome"][1][:]
        for i in range(self.size):
            self.individuals[i] = self.new_individuals[i][:]
            
    def evolve(self):
        i = 1
        self.new_individuals[0] = self.elitists["chromosome"][:]
        while True:
            s_chromo1 = self.select()
            s_chromo2 = self.select()
            (n_chromo1, n_chromo2) = self.cross(
            self.individuals[s_chromo1],
            self.individuals[s_chromo2])
            print(s_chromo1, self.fitness[s_chromo1], self.selector_probability[s_chromo1])
            print(s_chromo2, self.fitness[s_chromo2], self.selector_probability[s_chromo2])
            if random.randint(0, 1) == 0:
                self.new_individuals[i] = self.mutate(n_chromo1)
            else:
                self.new_individuals[i] = self.mutate(n_chromo2)
            
            i += 1
            if i >= self.size:
                break
        for i in range(self.size):
            self.individuals[i] = self.new_individuals[i][:]
    
    def getElitist(self, age):
        self.elitists["chromosome"] = []
        self.elitists["age"] = age
        bestIndividual = [[idx, fit] for idx, fit in sorted(
            enumerate(self.fitness), key=lambda x: x[1], reverse=True
        )][0]
        self.elitists["chromosome"].extend(self.individuals[bestIndividual[0]])
        self.elitists["fitness"] = self.fitness[bestIndividual[0]]


In [12]:
m = Population(10, 200, 243, 0.90, 0.1, 2000)
# len(m.individuals)
# n = m.genMap()
# for i in m.map:
#     print("".join(map(str, i)))
# m.lookAround((1,3))

In [13]:
mOld = m.fitness_func()

135 -622.82 0.6868333820206676
76 -576.73 0.3979997348564533
149 -486.84 0.7524662697162412
168 -300.47 0.8575143859197477
173 -493.66 0.8837449527039661
33 -469.84 0.18748633609893522
73 -367.02 0.3810312649776297
123 -480.1 0.6323273803916213
13 -817.0 0.08107386900994519
0 -680.83 0.009347789004896905
120 -517.74 0.6158791583637501
73 -367.02 0.3810312649776297
102 -459.29 0.5163922442913236
39 -621.15 0.22008474016425444
75 -372.52 0.39308471927904587
139 -538.86 0.7036258962600324
170 -534.36 0.8658774328690686
153 -504.84 0.7701116713266969
52 -368.91 0.2871455307312394
191 -681.44 0.9643366692000807
26 -446.11 0.1499113364642023
81 -739.64 0.41772576932636923
134 -617.83 0.6823314991698348
104 -308.0 0.5284538554766882
130 -434.18 0.6608374825131192
157 -575.69 0.7919327700661356
4 -714.57 0.031073604583487527
36 -622.91 0.20319622567534285
189 -641.99 0.9592714235402824
158 -439.42 0.798078578758882
173 -493.66 0.8837449527039661
28 -538.53 0.16135194883643839
102 -459.29 0.516

194 -246.44 0.9827025994812505
145 -589.24 0.7364436843849397
101 -438.71 0.49341784311762854
81 -446.11 0.3961235183617702
0 -305.0 0.01108550134935128
122 -371.12 0.6186701479961868
131 -480.51 0.6721227039891624
55 -756.71 0.2636619994110863
157 -913.73 0.7968351711785953
152 -372.31 0.7748101821842871
57 -752.92 0.27267707016335085
150 -635.97 0.7615616858096058
179 -787.51 0.9114754867042495
194 -246.44 0.9827025994812505
147 -465.49 0.7458250041544664
91 -874.35 0.4474119860487674
63 -220.86 0.31061718850976633
80 -433.69 0.3896506895442528
119 -485.3 0.5966880398984271
102 -448.07 0.4998668627121332
33 -661.07 0.15897223844596722
121 -283.49 0.6112863734471772
123 -288.44 0.6270582830343253
108 -549.12 0.535775422662299
23 -626.39 0.11736331319429402
159 -577.34 0.808056846706504
188 -745.84 0.9501790793702314
46 -335.66 0.22636922468423637
37 -475.94 0.17984053651411602
9 -379.06 0.05536567565229987
105 -600.54 0.517735441631933
23 -626.39 0.11736331319429402
40 -594.43 0.19194

107 -511.43 0.5374469215592449
196 -353.21 0.9898214673250494
77 -472.51 0.3965147379640154
172 -496.5 0.8610209135691775
75 -307.49 0.38720898011648786
101 -531.13 0.5034472770867635
163 -170.17 0.8204619314599948
198 -633.64 0.9999999999999997
63 -670.02 0.3292911919721443
39 -650.22 0.20718541084379416
62 -409.83 0.32550088971486885
184 -409.19 0.9212043149058962
124 -481.11 0.6181374164209507
32 -514.28 0.17259811334876116
7 -400.84 0.04666046925706782
76 -665.38 0.3910388802538771
103 -294.65 0.5157856863733539
48 -220.92 0.2549513778142124
107 -511.43 0.5374469215592449
145 -462.15 0.7212319480817172
22 -609.91 0.12380558840444357
184 -409.19 0.9212043149058962
174 -446.14 0.8711578855380601
135 -407.74 0.6734584711685189
151 -467.48 0.7535036229926796
47 -568.66 0.24732844453126396
45 -283.43 0.2390256907461888
152 -527.63 0.7585090851959483
18 -510.82 0.10218779141031523
111 -754.91 0.5522181256053289
97 -587.15 0.4845952725422241
78 -808.28 0.3991251258022092
180 -548.11 0.902

69 -268.57 0.3621936530485961
77 -472.06 0.4014469154646732
14 -434.68 0.08884645762409138
159 -421.36 0.8160203095963711
132 -451.69 0.6715344515773609
125 -663.17 0.642393529410485
159 -421.36 0.8160203095963711
48 -356.53 0.2508377378441465
140 -407.04 0.7145128353117404
106 -481.01 0.5413351640755448
148 -581.06 0.756631258297957
180 -457.33 0.9126385199553424
98 -794.7 0.5032431187199667
145 -304.28 0.740479914207963
194 -513.76 0.979935924522691
49 -395.5 0.25650872289302673
5 -710.15 0.03488092011599268
142 -304.61 0.7239259698619162
106 -481.01 0.5413351640755448
156 -421.41 0.798401391180046
100 -578.07 0.512705087398462
110 -303.57 0.5623822232970899
114 -320.4 0.5867608052635239
109 -582.79 0.5560216343439998
56 -614.77 0.292922404520465
97 -471.18 0.5005666934291693
17 -618.68 0.1008625787375305
130 -570.23 0.6605571996545453
155 -591.8 0.7929247674621576
69 -268.57 0.3621936530485961
135 -523.87 0.6866524775143591
72 -454.79 0.37576879058117935
27 -303.54 0.154043619603594

159 -588.15 0.8053620682176459
185 -295.94 0.9373196878223855
181 -431.64 0.9153255378918335
3 -429.51 0.02513916134040179
30 -314.99 0.1547493518544077
155 -258.67 0.7874416729633427
26 -398.67 0.13272013669373098
0 -195.98 0.010493967779421503
80 -437.1 0.4080101604234278
182 -398.27 0.9207422059487738
30 -314.99 0.1547493518544077
155 -258.67 0.7874416729633427
101 -423.96 0.5075387514776082
152 -291.71 0.7709979606960025
100 -474.05 0.5022779356286095
74 -458.53 0.37797290816640694
130 -392.18 0.6575452579584575
148 -570.24 0.7506521192472624
78 -350.96 0.3977761485455361
116 -424.11 0.5849372996678815
39 -332.8 0.20514949284332606
108 -322.53 0.5448929888649696
113 -504.24 0.5706579250301742
171 -401.6 0.8660614982256569
89 -306.56 0.4516547239629291
51 -471.49 0.2664841009817961
115 -495.2 0.5796773938162044
104 -262.0 0.5229426401388293
161 -472.61 0.8139642728984902
136 -410.11 0.689482645289414
158 -274.58 0.8010973354368427
156 -654.12 0.7913061889221173
124 -305.23 0.6277464

...

86 -1.11 0.4355174899190276
194 3.07 0.9784744453030131
147 0.03 0.7503814860749465
124 2.19 0.6308903073316752
148 3.02 0.7567320117140574
156 0.31 0.7984649649682147
179 3.17 0.9089563190327459
103 2.85 0.5211132250670442
134 0.83 0.6820386615845143
94 3.14 0.4842373200522068
14 -5.24 0.07779718576910838
185 1.22 0.9362285150289276
80 2.19 0.4117971727823485
140 1.33 0.7173431686395718
161 -0.51 0.8206333642851112
139 2.91 0.7120900242203072
77 1.66 0.39960260514405577
50 4.36 0.2637091485230808
45 1.1 0.24008623208638796
181 -0.28 0.9171899248715931
41 3.04 0.21756719024954063
112 0.6 0.5735537619397025
22 2.49 0.1152834685038603
100 1.93 0.5066329876690714
143 0.32 0.7320182074375173
188 0.66 0.9478581586072995
92 2.88 0.4711661461140368
31 4.74 0.16153581423738503
50 4.36 0.2637091485230808
9 1.67 0.05947936079167289
147 0.03 0.7503814860749465
37 2.82 0.19430790309279694
104 2.34 0.5270222008662169
126 2.28 0.6408966059102743
3 3.4 0.030791607955689172
183 1.77 0.9258066401303867

21 -1.89 0.11505657572826583
174 1.42 0.8843344617660445
142 0.17 0.7221157402139281
41 3.67 0.21716580848884845
113 1.17 0.5757700486458809
124 3.13 0.6312496444014564
125 2.16 0.6364102682635411
198 0.83 0.9999999999999999
71 -1.7 0.3633870405666819
33 1.93 0.17572613222576244
41 3.67 0.21716580848884845
118 2.55 0.6009490925125172
76 4.13 0.38936618115612204
168 -2.36 0.85424460201411
93 -4.47 0.47443424271734186
22 -0.78 0.11995583466090125
41 3.67 0.21716580848884845
88 4.7 0.44981348856395087
125 2.16 0.6364102682635411
103 4.63 0.5245914172735548
5 1.47 0.03563275204824762
173 2.0 0.8792396236345015
16 3.43 0.09073185736231225
90 -1.57 0.45984581247155215
122 4.44 0.6208795018775602
77 3.27 0.39462548361401917
83 -0.39 0.4243108500227584
135 -6.48 0.6867968038802913
68 2.88 0.34821276172052806
65 2.09 0.3326313225421029
108 0.6 0.5510523938893948
59 -5.48 0.3028712804392354
124 3.13 0.6312496444014564
60 -0.65 0.3077820963245335
22 -0.78 0.11995583466090125
23 2.22 0.12512179250

140 2.74 0.7222240973886433
136 -0.45 0.699727725835668
164 3.69 0.8259076743060949
191 0.05 0.9620166289758216
187 4.44 0.9429686884711019
88 2.62 0.4493311281376222
57 2.18 0.28323826239578764
131 1.59 0.6726296958855099
87 2.2 0.4431543299467828
28 3.01 0.14081187205364476
132 -2.57 0.6758868599588215
94 3.52 0.4784712143202709
44 -4.35 0.2193213397689045
128 5.2 0.6568557959518908
87 2.2 0.4431543299467828
29 2.32 0.14681990526659242
160 1.15 0.8092055669940709
193 2.95 0.9747808868037039
78 -0.01 0.3935092989502818
59 2.03 0.2940898504742296
36 3.18 0.18743600994588272
28 3.01 0.14081187205364476
189 1.68 0.952610794207986
54 -2.63 0.26643489609702864
131 1.59 0.6726296958855099
185 -4.6 0.932308367367604
4 1.63 0.028245631799822236
30 1.4 0.15231039254733858
36 3.18 0.18743600994588272
61 0.44 0.30545335898560994
140 2.74 0.7222240973886433
1 -1.95 0.01312428978071804
23 -1.06 0.1126224952464531
53 0.27 0.2632114850192955
187 4.44 0.9429686884711019
81 4.32 0.4093000753816901
36 

8 -3.07 0.050718358370895736
160 3.85 0.8092452483650129
55 0.59 0.2866596598710456
61 -0.61 0.31708662939957555
32 3.6 0.17170452035409395
71 -1.62 0.36190261201366053
96 -1.39 0.4858112388678116
166 2.27 0.8394869342680036
75 2.93 0.38240193924800703
148 3.06 0.7486477936280227
102 1.51 0.5163992190578365
28 0.09 0.15105308254506877
67 3.37 0.3472967604493084
113 2.45 0.5718726510850416
51 2.37 0.2670907962584033
47 3.21 0.24716431097550606
189 1.22 0.9548102137396296
100 3.36 0.5061608828238839
20 3.29 0.11112162939553034
19 3.68 0.1059069876199792
51 2.37 0.2670907962584033
19 3.68 0.1059069876199792
11 2.44 0.065786205350894
39 2.53 0.20676115322470368
50 0.94 0.26195059157258854
15 2.38 0.08522723135290217
74 1.21 0.37721642502930924
124 -0.05 0.6275629215910438
59 2.89 0.3072706427399966
31 3.89 0.16646479651569687
148 3.06 0.7486477936280227
83 3.33 0.42258583122360793
180 -1.43 0.9094076344944703
179 2.09 0.9045748873532186
42 0.43 0.22160730713309587
4 2.73 0.0309091924142132

KeyboardInterrupt: 

In [18]:
a.append(m.log)

In [20]:
a[1]

[[0, -169.505, -577.9057249999997, -1220.66],
 [1, -180.575, -557.1205499999998, -1101.01],
 [2, -240.19, -520.3720500000003, -955.93],
 [3, -148.25, -498.30807500000014, -883.46],
 [4, -123.565, -471.9982500000003, -832.91],
 [5, -130.175, -416.3780000000001, -774.315],
 [6, -118.94, -379.398575, -780.145],
 [7, -101.95, -340.5626999999999, -718.005],
 [8, -94.315, -324.28779999999995, -678.665],
 [9, -86.485, -287.003475, -660.35],
 [10, -62.925, -261.980375, -579.74],
 [11, -68.04, -244.94049999999993, -583.015],
 [12, -67.355, -226.6496249999999, -475.665],
 [13, -68.85, -210.36114999999987, -521.28],
 [14, -47.98, -191.31215, -530.405],
 [15, -49.805, -190.10945000000007, -434.085],
 [16, -44.4, -175.16435, -390.255],
 [17, -43.11, -160.599425, -355.15],
 [18, -32.885, -155.60407500000008, -326.385],
 [19, -37.735, -140.54685000000012, -306.27],
 [20, -26.925, -133.17657500000004, -301.84],
 [21, -24.9, -129.9301, -325.655],
 [22, -22.795, -122.46994999999998, -287.325],
 [23, -16

In [133]:
m.lookAround((6, 3)), m.strategyMX[m.lookAround((6, 3))]

((0, 1, 0, 0, 1), [0, 1, 2, 3, 4, 5, 6])

In [193]:
m.initPos()

AttributeError: 'Population' object has no attribute 'initPos'